In [1]:
%load_ext autoreload
%autoreload 2
import os
import sys
import numpy as np
import pandas as pd
import pingouin as pg
import plotly.graph_objects as go
from os.path import join as pjoin

sys.path.append("../..")
import circletrack_behavior as ctb
import plotting_functions as pf

/home/austinbaggetta/.conda/envs/calcium/lib/python3.10/site-packages/outdated/utils.py:14: OutdatedPackageWarning: The package pingouin is out of date. Your version is 0.5.2, the latest is 0.5.4.
Set the environment variable OUTDATED_IGNORE=1 to disable these warnings.
  return warn(


In [2]:
## Settings
lin_path = '../../../MultiCon_Behavior/MultiCon_Lesion1/output/lin_behav/'
circle_path = '../../../MultiCon_Behavior/MultiCon_Lesion1/output/behav/'
fig_path = '../../../MultiCon_Behavior/MultiCon_Lesion1/intermediate_figures'
sham_mice = ['mcls01', 'mcls02', 'mcls05', 'mcls06', 'mcls09', 'mcls10', 'mcls13', 'mcls14', 'mcls17', 'mcls18', 'mcls20', 'mcls22']
lesion_mice = ['mcls04', 'mcls07', 'mcls08', 'mcls11', 'mcls12', 'mcls15', 'mcls16', 'mcls19', 'mcls21', 'mcls23']
male_mice = [f'mcls0{x}' for x in np.arange(1, 3)] + [f'mcls0{x}' for x in np.arange(4, 9)] + ['mcls17', 'mcls18', 'mcls19']
female_mice = ['mcls09'] + [f'mcls{x}' for x in np.arange(10, 17)] + [f'mcls{x}' for x in np.arange(20, 24)]
bprobe_mice = ['mcls01', 'mcls05', 'mcls17', 'mcls19', 'mcls20']
two_color_plots = ['turquoise', 'darkgrey']
four_color_plots = ['orchid', 'lightblue', 'darkorchid', 'blue']
group_colors_dict = {'Sham': 'darkgrey', 'Lesion': 'turquoise'}
chance_color = 'darkgrey'

In [4]:
result_dict = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'rewards': []}
for mouse in os.listdir(lin_path):
    mouse_path = pjoin(lin_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'male' if mouse in male_mice else 'female'
    for idx, session in enumerate(os.listdir(mouse_path)):
        behav = pd.read_feather(pjoin(mouse_path, f'{session}'))
        result_dict['mouse'].append(mouse)
        result_dict['day'].append(idx+1)
        result_dict['group'].append(group)
        result_dict['sex'].append(sex)
        result_dict['rewards'].append(np.sum(behav['water']))
results_df = pd.DataFrame(result_dict)

In [5]:
## Plot rewards across days between sham and lesion 
fig = pf.plot_behavior_across_days(results_df, x_var='day', y_var='rewards', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=False,
                                   x_title='Day', y_title='Rewards', titles=['Linear Track'], height=500, width=500)
fig.show()
fig.write_image(pjoin(fig_path, 'linear_track_rewards.png'))
results_df.mixed_anova(dv='rewards', within='day', subject='mouse', between='group')

Source            SS  DF1  DF2           MS          F         p-unc  \
0        group   2169.992727    1   20  2169.992727   2.046084  1.680368e-01   
1          day  12508.454545    4   80  3127.113636  22.573711  1.667515e-12   
2  Interaction    376.825455    4   80    94.206364   0.680048  6.077971e-01   

   p-GG-corr       np2       eps sphericity   W-spher       p-spher  
0        NaN  0.092809       NaN        NaN       NaN           NaN  
1   0.000002  0.530227  0.401937      False  0.064771  3.160520e-08  
2        NaN  0.032884       NaN        NaN       NaN           NaN

In [5]:
result_dict = {'mouse': [], 'day': [], 'group': [], 'rewards': []}
for mouse in os.listdir(lin_path):
    mouse_path = pjoin(lin_path, mouse)
    group = 'Sham Male' if mouse in male_mice and mouse in sham_mice else 'Lesion Male' if mouse in male_mice and mouse in lesion_mice else 'Sham Female' if mouse in female_mice and mouse in sham_mice  else 'Lesion Female' if mouse in lesion_mice and mouse in female_mice else 'None'
    for idx, session in enumerate(os.listdir(mouse_path)):
        behav = pd.read_feather(pjoin(mouse_path, f'{session}'))
        result_dict['mouse'].append(mouse)
        result_dict['day'].append(idx+1)
        result_dict['group'].append(group)
        result_dict['rewards'].append(np.sum(behav['water']))
results_two = pd.DataFrame(result_dict)

In [6]:
## Plot rewards across days between sham and lesion male and female
fig = pf.plot_behavior_across_days(results_two, x_var='day', y_var='rewards', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=four_color_plots, avg_color='darkgrey', expert_line=False, chance=False,
                                   x_title='Day', y_title='Rewards', titles=['Linear Track'], height=500, width=600)
fig.show()
results_two.mixed_anova(dv='rewards', within='day', subject='mouse', between='group')

Source            SS  DF1  DF2           MS          F         p-unc  \
0        group   5273.822727    3   18  1757.940909   1.747519  1.932205e-01   
1          day  12508.454545    4   72  3127.113636  24.253203  9.876424e-13   
2  Interaction   2175.745455   12   72   181.312121   1.406217  1.831874e-01   

   p-GG-corr       np2       eps sphericity   W-spher       p-spher  
0        NaN  0.225559       NaN        NaN       NaN           NaN  
1   0.000002  0.573997  0.401937      False  0.064771  3.160520e-08  
2        NaN  0.189870       NaN        NaN       NaN           NaN

In [7]:
## Position across time
fig = pf.custom_graph_template(x_title='Time (s)', y_title='X Position')
fig.add_trace(go.Scatter(x=behav['t'], y=behav['x'], mode='lines', line_color='darkgrey', showlegend=False))
fig.add_trace(go.Scatter(x=behav['t'][behav['lick_port'] != -1], y=behav['x'][behav['lick_port'] != -1], mode='markers', marker_color='red', showlegend=False))
fig.show()

### Plot performance of individual mice across trials for each group.

In [8]:
## Circle track accuracy across trials
## Plots individual mice
bin_size = 4
chance_color = 'darkgrey'
opacity = 0.8
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               rows=2, columns=2, shared_x=True, shared_y=True,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for mouse in os.listdir(circle_path):
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'male' if mouse in male_mice else 'female'
    for session in os.listdir(mouse_path):
        if '_20' in session:
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
            pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=True)
            binned_pc = ctb.bin_data(pc, bin_size=bin_size)
            x_data = np.arange(1, len(binned_pc)+1) * bin_size
            if (group == 'Sham') & (sex == 'male'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[0], showlegend=False, name=mouse), row=1, col=1)
            elif (group == 'Lesion') & (sex == 'male'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[1], showlegend=False, name=mouse), row=1, col=2)
            elif (group == 'Sham') & (sex == 'female'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[2], showlegend=False, name=mouse), row=2, col=1)
            elif (group == 'Lesion') & (sex == 'female'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[3], showlegend=False, name=mouse), row=2, col=2)
        else:
            pass
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy', col=1)
fig.update_xaxes(title='Trial', row=2)
fig.show()

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:983: RuntimeWarning:

Mean of empty slice

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/A

In [9]:
## Circle track accuracy across trials but just the first 15 minutes
## Plots individual mice
bin_size = 4
chance_color = 'darkgrey'
opacity = 0.8
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               rows=2, columns=2, shared_x=True, shared_y=True,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for mouse in os.listdir(circle_path):
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'male' if mouse in male_mice else 'female'
    for session in os.listdir(mouse_path):
        if '_10' in session:
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            behav_data = behav_data[behav_data['t'] <= 900] ## 900 seconds is 15 minutes
            reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
            pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=True)
            binned_pc = ctb.bin_data(pc, bin_size=bin_size)
            x_data = np.arange(1, len(binned_pc)+1) * bin_size
            if (group == 'Sham') & (sex == 'male'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[0], showlegend=False, name=mouse), row=1, col=1)
            elif (group == 'Lesion') & (sex == 'male'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[1], showlegend=False, name=mouse), row=1, col=2)
            elif (group == 'Sham') & (sex == 'female'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[2], showlegend=False, name=mouse), row=2, col=1)
            elif (group == 'Lesion') & (sex == 'female'):
                fig.add_trace(go.Scatter(x=x_data, y=binned_pc, mode='lines', opacity=opacity,
                                        line_color=four_color_plots[3], showlegend=False, name=mouse), row=2, col=2)
        else:
            pass
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy', col=1)
fig.update_xaxes(title='Trial', row=2)
fig.show()

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide



In [10]:
result_dict = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'rewards': [], 'percent_correct': []}
for mouse in os.listdir(circle_path):
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'Male' if mouse in male_mice else 'Female'
    for idx, session in enumerate(os.listdir(mouse_path)):
        behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
        reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
        pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=False)
        result_dict['mouse'].append(mouse)
        result_dict['day'].append(idx+1)
        result_dict['group'].append(group)
        result_dict['sex'].append(sex)
        result_dict['rewards'].append(np.sum(behav_data['water']))
        result_dict['percent_correct'].append(pc)
circletrack_df = pd.DataFrame(result_dict)

In [11]:
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               shared_y=True, shared_x=True, rows=2, columns=2,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for mouse in np.unique(circletrack_df['mouse']):
    mouse_data = circletrack_df[circletrack_df['mouse'] == mouse]
    if ('Sham' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 1
        color_idx = 0
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 2
        color_idx = 1
    elif ('Sham' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 1
        color_idx = 2
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 2
        color_idx = 3
    
    fig.add_trace(go.Scatter(x=mouse_data['percent_correct'], y=mouse_data['rewards'], mode='markers', 
                                marker_color=four_color_plots[color_idx], showlegend=False, name=mouse, opacity=opacity,
                                marker=dict(line=dict(width=0.5))), row=row, col=col)
fig.update_yaxes(title='Rewards', col=1)
fig.update_xaxes(title='Lick Accuracy (%)', row=2)
fig.show()

In [12]:
## Lick accuracy across days for the whole session
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               shared_y=True, shared_x=True, rows=2, columns=2,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for mouse in np.unique(circletrack_df['mouse']):
    mouse_data = circletrack_df[circletrack_df['mouse'] == mouse]
    if ('Sham' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 1
        color_idx = 0
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 2
        color_idx = 1
    elif ('Sham' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 1
        color_idx = 2
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 2
        color_idx = 3
    
    fig.add_trace(go.Scatter(x=mouse_data['day'], y=mouse_data['percent_correct'], mode='lines', 
                                marker_color=four_color_plots[color_idx], showlegend=False, name=mouse, opacity=opacity), row=row, col=col)
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy (%)', col=1)
fig.update_xaxes(title='Day', row=2)
fig.show()

In [13]:
## Lick accuracy across days for just the first 15 minutes
result_dict = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'rewards': [], 'percent_correct': []}
for mouse in os.listdir(circle_path):
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'Male' if mouse in male_mice else 'Female'
    for idx, session in enumerate(os.listdir(mouse_path)):
        behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
        behav_data = behav_data[behav_data['t'] <= 900]
        reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
        pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=False)
        result_dict['mouse'].append(mouse)
        result_dict['day'].append(idx+1)
        result_dict['group'].append(group)
        result_dict['sex'].append(sex)
        result_dict['rewards'].append(np.sum(behav_data['water']))
        result_dict['percent_correct'].append(pc)
df_first_fift = pd.DataFrame(result_dict)

In [14]:
## Lick accuracy across days for just the first 15 minutes
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               rows=2, columns=2, shared_x=True, shared_y=True,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for mouse in np.unique(df_first_fift['mouse']):
    mouse_data = df_first_fift[df_first_fift['mouse'] == mouse]
    if ('Sham' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 1
        color_idx = 0
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 2
        color_idx = 1
    elif ('Sham' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 1
        color_idx = 2
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 2
        color_idx = 3
    
    fig.add_trace(go.Scatter(x=mouse_data['day'], y=mouse_data['percent_correct'], mode='lines+markers', 
                             marker_color=four_color_plots[color_idx], showlegend=False, name=mouse, opacity=opacity), row=row, col=col)
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy (%)', col=1)
fig.update_xaxes(title='Day', row=2)
fig.show()

In [15]:
## Lick accuracy across days for just the first 10 minutes
result_dict = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'rewards': [], 'percent_correct': []}
for mouse in os.listdir(circle_path):
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'Male' if mouse in male_mice else 'Female'
    for idx, session in enumerate(os.listdir(mouse_path)):
        behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
        behav_data = behav_data[behav_data['t'] <= 600]
        reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
        pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=False)
        result_dict['mouse'].append(mouse)
        result_dict['day'].append(idx+1)
        result_dict['group'].append(group)
        result_dict['sex'].append(sex)
        result_dict['rewards'].append(np.sum(behav_data['water']))
        result_dict['percent_correct'].append(pc)
df_first_ten = pd.DataFrame(result_dict)

In [16]:
## Lick accuracy across days for just the first 10 minutes
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               rows=2, columns=2, shared_x=True, shared_y=True,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for mouse in np.unique(df_first_ten['mouse']):
    mouse_data = df_first_ten[df_first_ten['mouse'] == mouse]
    if ('Sham' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 1
        color_idx = 0
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Male' in mouse_data['sex'].to_numpy()):
        row = 1
        col = 2
        color_idx = 1
    elif ('Sham' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 1
        color_idx = 2
    elif ('Lesion' in mouse_data['group'].to_numpy()) and ('Female' in mouse_data['sex'].to_numpy()):
        row = 2
        col = 2
        color_idx = 3
    
    fig.add_trace(go.Scatter(x=mouse_data['day'], y=mouse_data['percent_correct'], mode='lines+markers', 
                             marker_color=four_color_plots[color_idx], showlegend=False, name=mouse, opacity=opacity), row=row, col=col)
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy (%)', col=1)
fig.update_xaxes(title='Day', row=2)
fig.show()

In [17]:
## Lick distribution for an individual mouse
mouse = 'mcls04' 
day = 15
behav_data = pd.read_feather(pjoin(circle_path, f'{mouse}/{mouse}_{day}.feat'))
reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
fig = pf.custom_graph_template(x_title='Time (s)', y_title='', width=1100, rows=1, columns=2)
fig.add_trace(go.Histogram(x=behav_data['t'][(behav_data['lick_port'] == reward_one) | (behav_data['lick_port'] == reward_two)],
                           marker_color='darkgrey', marker_line_width=1, marker_line_color='black',
                           name='Correct Licks'), row=1, col=1)
fig.add_trace(go.Histogram(x=behav_data['t'][(behav_data['lick_port'] != reward_one) & (behav_data['lick_port'] != reward_two) & (behav_data['lick_port'] != -1)],
                           marker_color='red', marker_line_width=1, marker_line_color='black',
                           name='Incorrect Licks'), row=1, col=1)
fifteen_minute_mark = 60 * 15
first_incorrect_lick = behav_data['t'][(behav_data['lick_port'] != reward_one) & (behav_data['lick_port'] != reward_two) & (behav_data['lick_port'] != -1)].reset_index(drop=True)[0]
binned = np.histogram(behav_data['t'][behav_data['water']], bins=25, density=False)
plot_y = np.cumsum(binned[0])
fig.add_trace(go.Scatter(x=binned[1], y=plot_y, mode='lines+markers',
                         line_color='darkgrey', name='Rewards',showlegend=False), row=1, col=2)
fig.add_vline(x=fifteen_minute_mark, line_width=1, line_dash='dash', line_color='black', opacity=1)
fig.add_vline(x=first_incorrect_lick, line_width=1, line_dash='dash', line_color='red', opacity=1, col=2)
fig.update_yaxes(title='Licks', col=1)
fig.update_yaxes(title='Rewards', col=2)
fig.show()

In [18]:
## Average circle track accuracy across trials for two days of interest
bin_size = 4
chance_color = 'darkgrey'
opacity = 0.8
days_of_interest = ('1', '21')
data = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'trial_acc': []}
for mouse in os.listdir(circle_path):
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'male' if mouse in male_mice else 'female'
    for session in os.listdir(mouse_path):
        if session == f'{mouse}_{days_of_interest[0]}.feat':
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
            pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=True)
            binned_pc = ctb.bin_data(pc, bin_size=bin_size)
            x_data = np.arange(1, len(binned_pc)+1) * bin_size
            data['mouse'].append(mouse)
            data['day'].append(days_of_interest[0])
            data['group'].append(group)
            data['sex'].append(sex)
            data['trial_acc'].append(binned_pc)
        elif session == f'{mouse}_{days_of_interest[1]}.feat':
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
            pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=True)
            binned_pc = ctb.bin_data(pc, bin_size=bin_size)
            x_data = np.arange(1, len(binned_pc)+1) * bin_size
            data['mouse'].append(mouse)
            data['day'].append(days_of_interest[1])
            data['group'].append(group)
            data['sex'].append(sex)
            data['trial_acc'].append(binned_pc)
        else:
            pass
trial_acc = pd.DataFrame(data)
day_data = {}
for day in days_of_interest:
    group_data = {}
    group_data['Sham Males'] = np.nanmean(trial_acc['trial_acc'][(trial_acc['group'] == 'Sham') & (trial_acc['sex'] == 'male') & (trial_acc['day'] == day)].apply(pd.Series), axis=0)
    group_data['Lesion Males'] = np.nanmean(trial_acc['trial_acc'][(trial_acc['group'] == 'Lesion') & (trial_acc['sex'] == 'male') & (trial_acc['day'] == day)].apply(pd.Series), axis=0)
    group_data['Sham Females'] = np.nanmean(trial_acc['trial_acc'][(trial_acc['group'] == 'Sham') & (trial_acc['sex'] == 'female') & (trial_acc['day'] == day)].apply(pd.Series), axis=0)
    group_data['Lesion Females'] = np.nanmean(trial_acc['trial_acc'][(trial_acc['group'] == 'Lesion') & (trial_acc['sex'] == 'female') & (trial_acc['day'] == day)].apply(pd.Series), axis=0)
    day_data[day] = group_data

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/medi

In [19]:
fig = pf.custom_graph_template(x_title='', y_title='', height=700, width=700,
                               rows=2, columns=2, shared_x=True, shared_y=True,
                               titles=['Sham Male', 'Lesion Male', 'Sham Female', 'Lesion Female'])
for day in days_of_interest:
    plot_data = day_data[day]
    if day == days_of_interest[0]:
        legendgroup = 'first'
        dashtype = 'dot'
    else:
        legendgroup = 'second' 
        dashtype = 'dash'
    for group in plot_data.keys():
        group_data = plot_data[group]
        x_data = np.arange(1, len(group_data)+1) * bin_size
        if group == 'Sham Males':
            row, col, idx = 1, 1, 0
        elif group == 'Lesion Males':
            row, col, idx = 1, 2, 1
        elif group == 'Sham Females':
            row, col, idx = 2, 1, 2
        else:
            row, col, idx = 2, 2, 3
        fig.add_trace(go.Scatter(x=x_data, y=group_data, mode='lines', opacity=opacity,
                                line_color=four_color_plots[idx], showlegend=True if group == 'Sham Males' else False, name=f'Day {day}',
                                legendgroup=legendgroup, line=dict(dash=dashtype)), row=row, col=col)
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy', col=1)
fig.update_xaxes(title='Trial', row=2)
fig.show()

### Look at probe performance for mice that got continually probed in B.

In [20]:
## Probe accuracy for mice that got probed continually in B
result_dict = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'rewards': [], 'percent_correct': []}
for mouse in bprobe_mice:
    mouse_path = pjoin(circle_path, mouse)
    group = 'Sham' if mouse in sham_mice else 'Lesion' 
    sex = 'Male' if mouse in male_mice else 'Female'
    for idx, session in enumerate(os.listdir(mouse_path)):
        behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
        reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
        behav_data = behav_data[behav_data['probe']]
        pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=False)
        result_dict['mouse'].append(mouse)
        result_dict['day'].append(idx+1)
        result_dict['group'].append(group)
        result_dict['sex'].append(sex)
        result_dict['rewards'].append(np.sum(behav_data['water']))
        result_dict['percent_correct'].append(pc)
circletrack_df = pd.DataFrame(result_dict)
plot_data = circletrack_df[circletrack_df['day'] > 15] ## day 16 starts probe in B
probe_data = pd.DataFrame()
for mouse in bprobe_mice:
    mouse_data = plot_data[plot_data['mouse'] == mouse]
    probe_data = pd.concat([probe_data, mouse_data])

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1073: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1073: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1073: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1073: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1073: RuntimeWarning:

invalid value encountered in scalar divide

/medi

In [22]:
## Probe accuracy for mice that got probed continually in B
fig = pf.plot_behavior_across_days(probe_data, x_var='day', y_var='percent_correct', plot_transitions=None,
                                   x_title='Day', y_title='Probe Accuracy', groupby_var=['day'])
fig.update_yaxes(range=[0, 100], dtick=25)
fig.show()

### Analyze lick accuracy and rewards across days.

In [6]:
circletrack_results = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'group_two': [], 'session': [], 
                       'lick_accuracy': [], 'lick_accuracy_thresh3': [], 'rewards': []}
for mouse in os.listdir(circle_path):
    if mouse in bprobe_mice:
        pass
    else:
        mouse_path = pjoin(circle_path, mouse)
        group = 'Sham' if mouse in sham_mice else 'Lesion'
        sex = 'Male' if mouse in male_mice else 'Female'
        grouping = 'Sham Male' if mouse in sham_mice and mouse in male_mice else 'Lesion Male' if mouse not in sham_mice and mouse in male_mice else 'Sham Female' if mouse in sham_mice and mouse not in male_mice else 'Lesion Female'
        for idx, session in enumerate(os.listdir(mouse_path)):
            behav = pd.read_feather(pjoin(mouse_path, f'{session}'))
            if (np.unique(behav['session'])[0] == 'RM') | (idx == 20):
                pass 
            else:
                behav_data = behav[~behav['probe']]
                reward_one, reward_two = np.unique(behav['reward_one'])[0], np.unique(behav['reward_two'])[0]
                session_pc = ctb.lick_accuracy(behav, port_one=reward_one, port_two=reward_two, lick_threshold=1, by_trials=False)
                session_pc_thresh3 = ctb.lick_accuracy(behav, port_one=reward_one, port_two=reward_two, lick_threshold=3, by_trials=False)
                circletrack_results['mouse'].append(mouse)
                circletrack_results['day'].append(idx+1)
                circletrack_results['group'].append(group)
                circletrack_results['group_two'].append(grouping)
                circletrack_results['sex'].append(sex)
                circletrack_results['session'].append(np.unique(behav['session'])[0])
                circletrack_results['lick_accuracy'].append(session_pc)
                circletrack_results['lick_accuracy_thresh3'].append(session_pc_thresh3)
                circletrack_results['rewards'].append(np.sum(behav_data['water']))
ct_df = pd.DataFrame(circletrack_results)

In [7]:
## Plot lick accuracy (thresh1) across days
fig = pf.plot_behavior_across_days(ct_df, x_var='day', y_var='lick_accuracy', groupby_var=['day', 'group'], plot_transitions=[15.5],
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=True, plot_datapoints=False,
                                   x_title='Day', y_title='Lick Accuracy', titles=['Circle Track'], height=500, width=500)
fig.show()
fig.write_image(pjoin(fig_path, 'lick_accuracy.png'))
## Repeated measures ANOVA for reversal
anova_data = ct_df[ct_df['day'] >= 16] ## start of reversal
anova_data.mixed_anova(dv='lick_accuracy', within='day', subject='mouse', between='group')

Source           SS  DF1  DF2           MS          F         p-unc  \
0        group   171.854646    1   15   171.854646   0.995156  3.343070e-01   
1          day  6613.043050    4   60  1653.260762  52.981684  4.989122e-19   
2  Interaction    98.741971    4   60    24.685493   0.791091  5.355755e-01   

        np2      eps  
0  0.062216      NaN  
1  0.779352  0.78136  
2  0.050097      NaN

In [8]:
## Plot lick accuracy (thresh3) across days
fig = pf.plot_behavior_across_days(ct_df, x_var='day', y_var='lick_accuracy_thresh3', groupby_var=['day', 'group'], plot_transitions=[15.5],
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=True, plot_datapoints=False,
                                   x_title='Day', y_title='Lick Accuracy', titles=['Circle Track'], height=500, width=500)
fig.show()
fig.write_image(pjoin(fig_path, 'lick_accuracy_thresh3.png'))
## Repeated measures ANOVA for reversal
anova_data = ct_df[ct_df['day'] >= 16] ## start of reversal
anova_data.mixed_anova(dv='lick_accuracy', within='day', subject='mouse', between='group')

Source           SS  DF1  DF2           MS          F         p-unc  \
0        group   171.854646    1   15   171.854646   0.995156  3.343070e-01   
1          day  6613.043050    4   60  1653.260762  52.981684  4.989122e-19   
2  Interaction    98.741971    4   60    24.685493   0.791091  5.355755e-01   

        np2      eps  
0  0.062216      NaN  
1  0.779352  0.78136  
2  0.050097      NaN

In [14]:
## Plot lick accuracy across days without reversal
fig = pf.plot_behavior_across_days(ct_df[ct_df['day'] < 16], x_var='day', y_var='lick_accuracy', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=True, plot_datapoints=False,
                                   x_title='Day', y_title='Lick Accuracy', titles=['Circle Track'], height=500, width=500)
fig.show()
fig.write_image(pjoin(fig_path, 'lick_accuracy_without_reversal.png'))
## Repeated measures ANOVA for reversal
anova_data = ct_df[ct_df['day'] < 16] ## start of reversal
anova_data.mixed_anova(dv='lick_accuracy', within='day', subject='mouse', between='group')

Source            SS  DF1  DF2           MS          F         p-unc  \
0        group    591.152731    1   15   591.152731   1.206402  2.893640e-01   
1          day  31707.284914   14  210  2264.806065  42.221672  3.290700e-53   
2  Interaction    863.899035   14  210    61.707074   1.150375  3.161035e-01   

      p-GG-corr       np2       eps sphericity       W-spher       p-spher  
0           NaN  0.074440       NaN        NaN           NaN           NaN  
1  1.002386e-18  0.737862  0.314724      False  6.238400e-09  2.785703e-08  
2           NaN  0.071229       NaN        NaN           NaN           NaN

In [36]:
## Plot rewards across days
fig = pf.plot_behavior_across_days(ct_df, x_var='day', y_var='rewards', groupby_var=['day', 'group'], plot_transitions=[15.5],
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=False, plot_datapoints=False,
                                   x_title='Day', y_title='Rewards', titles=['Circle Track'], height=500, width=600)
fig.show()
fig.write_image(pjoin(fig_path, 'total_rewards.png'))
## Difference in rewards during reversal
anova_data = ct_df[ct_df['day'] >= 16]
anova_data.mixed_anova(dv='rewards', within='day', subject='mouse', between='group')

Source           SS  DF1  DF2           MS         F     p-unc  \
0        group  6206.302124    1   15  6206.302124  2.266337  0.152977   
1          day  4503.458824    4   60  1125.864706  4.161560  0.004850   
2  Interaction  3539.796732    4   60   884.949183  3.271059  0.017141   

        np2       eps  
0  0.131258       NaN  
1  0.217183  0.745088  
2  0.179030       NaN

In [21]:
## Plot rewards across days without reversal
fig = pf.plot_behavior_across_days(ct_df[ct_df['day'] < 16], x_var='day', y_var='rewards', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=False, plot_datapoints=False,
                                   x_title='Day', y_title='Rewards', titles=['Circle Track'], height=500, width=500)
fig.show()
fig.write_image(pjoin(fig_path, 'total_rewards_without_reversal.png'))
## Difference in rewards during reversal
anova_data = ct_df[ct_df['day'] < 16]
anova_data.mixed_anova(dv='rewards', within='day', subject='mouse', between='group')

Source             SS  DF1  DF2           MS          F         p-unc  \
0        group    1247.071078    1   15  1247.071078   0.224163  6.427029e-01   
1          day  103348.078431   14  210  7382.005602  31.868976  2.559168e-44   
2  Interaction    5249.004902   14  210   374.928922   1.618612  7.607951e-02   

      p-GG-corr       np2       eps sphericity       W-spher       p-spher  
0           NaN  0.014724       NaN        NaN           NaN           NaN  
1  6.132822e-13  0.679959  0.254524      False  7.523331e-09  4.693957e-08  
2           NaN  0.097398       NaN        NaN           NaN           NaN

In [92]:
## Separate into four groups
## Plot lick accuracy across days
fig = pf.plot_behavior_across_days(ct_df, x_var='day', y_var='lick_accuracy', groupby_var=['day', 'group_two'], plot_transitions=[15.5],
                                   marker_color=four_color_plots, avg_color='darkgrey', expert_line=True, chance=True, plot_datapoints=False,
                                   x_title='Day', y_title='Lick Accuracy', titles=['Circle Track'], height=500, width=600)
fig.show()

### Plot d', correct rejection rate, and hit rate for sham and lesion mice.

In [42]:
metrics = pd.DataFrame()
for mouse in os.listdir(circle_path):
    if mouse in bprobe_mice:
        pass
    else:
        mouse_path = pjoin(circle_path, mouse)
        group = 'Sham' if mouse in sham_mice else 'Lesion' 
        sex = 'Male' if mouse in male_mice else 'Female'
        for idx, session in enumerate(os.listdir(mouse_path)):
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            if (np.unique(behav_data['session'])[0] == 'RM') | (idx == 20):
                pass 
            else:
                reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
                signal = pd.DataFrame(ctb.dprime_metrics(behav_data, mouse, day=idx+1, reward_ports=[reward_one, reward_two], forward_reverse='forward'))
                signal['group'] = group
                signal['sex'] = sex
                metrics = pd.concat([metrics, signal], ignore_index=True)

In [49]:
## dprime across days
fig = pf.plot_behavior_across_days(data=metrics, x_var='day', y_var='dprime', groupby_var=['group', 'day'], plot_transitions=[15.5],
                                   x_title='Day', y_title="d'", marker_color=two_color_plots, expert_line=False, chance=False, plot_datapoints=False)
fig.show()
fig.write_image(pjoin(fig_path, 'dprime_across_days.png'))
## Repeated measures ANOVA during reversal
anova_data = metrics.groupby(['mouse', 'group', 'day'], as_index=False).agg({'dprime': 'mean'})
adata = anova_data[anova_data['day'] >= 16] ## start of reversal
adata.mixed_anova(dv='dprime', subject='mouse', within='day', between='group')

Source         SS  DF1  DF2        MS          F         p-unc  \
0        group   0.493249    1   15  0.493249   1.563062  2.303708e-01   
1          day  23.440582    4   60  5.860145  54.566399  2.514627e-19   
2  Interaction   0.804365    4   60  0.201091   1.872449  1.270024e-01   

      p-GG-corr       np2       eps sphericity  W-spher   p-spher  
0           NaN  0.094370       NaN        NaN      NaN       NaN  
1  6.243141e-13  0.784379  0.625757      False  0.18628  0.004184  
2           NaN  0.110977       NaN        NaN      NaN       NaN

In [67]:
## Repeated measures ANOVA during acquisition
anova_data = metrics.groupby(['mouse', 'group', 'day'], as_index=False).agg({'dprime': 'mean'})
adata = anova_data[anova_data['day'] < 16] ## start of reversal
adata.mixed_anova(dv='dprime', subject='mouse', within='day', between='group')

Source         SS  DF1  DF2        MS          F         p-unc  \
0        group   1.429091    1   15  1.429091   1.840941  1.949097e-01   
1          day  84.465838   14  210  6.033274  49.910834  7.479891e-59   
2  Interaction   2.817455   14  210  0.201247   1.664833  6.489988e-02   

      p-GG-corr       np2       eps sphericity       W-spher   p-spher  
0           NaN  0.109313       NaN        NaN           NaN       NaN  
1  1.013816e-17  0.768914  0.270785      False  5.630190e-07  0.001481  
2           NaN  0.099901       NaN        NaN           NaN       NaN

In [48]:
## Correct rejection across days
fig = pf.plot_behavior_across_days(data=metrics, x_var='day', y_var='CR', groupby_var=['group', 'day'], plot_transitions=[15.5],
                                   x_title='Day', y_title="Correct Rejection Rate", marker_color=two_color_plots, expert_line=False, chance=False, plot_datapoints=False)
fig.add_hline(y=1, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.show()
fig.write_image(pjoin(fig_path, 'CR_across_days.png'))
## Repeated measures ANOVA during reversal
anova_data = metrics.groupby(['mouse', 'group', 'day'], as_index=False).agg({'CR': 'mean'})
adata = anova_data[anova_data['day'] >= 16] ## start of reversal
adata.mixed_anova(dv='CR', subject='mouse', within='day', between='group')

Source        SS  DF1  DF2        MS          F         p-unc  \
0        group  0.025257    1   15  0.025257   0.538329  4.744386e-01   
1          day  1.570989    4   60  0.392747  44.927841  2.112417e-17   
2  Interaction  0.042641    4   60  0.010660   1.219456  3.120850e-01   

      p-GG-corr       np2       eps sphericity  W-spher   p-spher  
0           NaN  0.034645       NaN        NaN      NaN       NaN  
1  1.369323e-11  0.749699  0.604388      False  0.18384  0.003904  
2           NaN  0.075185       NaN        NaN      NaN       NaN

In [65]:
## Repeated measures ANOVA during acquisition
anova_data = metrics.groupby(['mouse', 'group', 'day'], as_index=False).agg({'CR': 'mean'})
adata = anova_data[anova_data['day'] < 16] ## start of reversal
adata.mixed_anova(dv='CR', subject='mouse', within='day', between='group')

Source        SS  DF1  DF2        MS          F         p-unc  \
0        group  0.000052    1   15  0.000052   0.000949  9.758288e-01   
1          day  5.714005   14  210  0.408143  26.235523  1.193742e-38   
2  Interaction  0.199550   14  210  0.014254   0.916223  5.421376e-01   

        np2       eps  
0  0.000063       NaN  
1  0.636236  0.243055  
2  0.057565       NaN

In [50]:
## Correct rejection across days
fig = pf.plot_behavior_across_days(data=metrics, x_var='day', y_var='hits', groupby_var=['group', 'day'], plot_transitions=[15.5],
                                   x_title='Day', y_title="Hit Rate", marker_color=two_color_plots, expert_line=False, chance=False, plot_datapoints=False)
fig.add_hline(y=1, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.show()
fig.write_image(pjoin(fig_path, 'HR_across_days.png'))
## Repeated measures ANOVA during reversal
anova_data = metrics.groupby(['mouse', 'group', 'day'], as_index=False).agg({'hits': 'mean'})
adata = anova_data[anova_data['day'] >= 16] ## start of reversal
adata.mixed_anova(dv='hits', subject='mouse', within='day', between='group')

Source        SS  DF1  DF2        MS          F         p-unc  \
0        group  0.019168    1   15  0.019168   1.582363  2.276510e-01   
1          day  0.761222    4   60  0.190306  20.893929  7.914281e-11   
2  Interaction  0.064532    4   60  0.016133   1.771278  1.464617e-01   

        np2       eps  
0  0.095424       NaN  
1  0.582102  0.363384  
2  0.105614       NaN

In [52]:
## Repeated measures ANOVA during acquisition
anova_data = metrics.groupby(['mouse', 'group', 'day'], as_index=False).agg({'hits': 'mean'})
adata = anova_data[anova_data['day'] < 16] ## start of reversal
adata.mixed_anova(dv='hits', subject='mouse', within='day', between='group')

Source        SS  DF1  DF2        MS          F         p-unc  \
0        group  0.388688    1   15  0.388688   4.200394  5.832372e-02   
1          day  2.672251   14  210  0.190875  11.577197  1.374755e-19   
2  Interaction  0.493884   14  210  0.035277   2.139693  1.115855e-02   

        np2      eps  
0  0.218766      NaN  
1  0.435606  0.16721  
2  0.124838      NaN

### Concatenate lick accuracy across all trials for sham vs lesion mice.

In [17]:
bin_size = 5
data = {'mouse': [], 'group': [], 'sex': [], 'trial_acc': []}
for mouse in os.listdir(circle_path):
    if mouse in bprobe_mice:
        pass
    else:
        mouse_path = pjoin(circle_path, mouse)
        group = 'Sham' if mouse in sham_mice else 'Lesion' 
        sex = 'Male' if mouse in male_mice else 'Female'
        accuracy = []
        for idx, session in enumerate(os.listdir(mouse_path)):
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
            pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=True)
            accuracy = np.concatenate((accuracy, pc))
        data['mouse'].append(mouse)
        data['group'].append(group)
        data['sex'].append(sex)
        data['trial_acc'].append(accuracy)
        
trial_data = pd.DataFrame(data)
data['binned_pc'] = []
for idx, mouse in enumerate(trial_data['mouse']):
    d = trial_data['trial_acc'][trial_data['mouse'] == mouse]
    data['binned_pc'].append(ctb.bin_data(d.values[0], bin_size=bin_size))
trial_data = pd.DataFrame(data)
group_data = {'Sham': [], 'Lesion': []}
group_data['Sham'].append(np.nanmean(trial_data['binned_pc'][trial_data['group'] == 'Sham'].apply(pd.Series), axis=0))
group_data['Lesion'].append(np.nanmean(trial_data['binned_pc'][trial_data['group'] == 'Lesion'].apply(pd.Series), axis=0))
group_data['Sham'].append(np.std(trial_data['binned_pc'][trial_data['group'] == 'Sham'].apply(pd.Series), axis=0, ddof=1).to_numpy() / np.sqrt(len(trial_data['binned_pc'][trial_data['group'] == 'Sham'].apply(pd.Series))))
group_data['Lesion'].append(np.std(trial_data['binned_pc'][trial_data['group'] == 'Lesion'].apply(pd.Series), axis=0, ddof=1).to_numpy() / np.sqrt(len(trial_data['binned_pc'][trial_data['group'] == 'Lesion'].apply(pd.Series))))
plot_data = pd.DataFrame(group_data)

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1068: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1068: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1068: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1068: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1068: RuntimeWarning:

invalid value encountered in scalar divide

/medi

In [20]:
data_points = 40 ## the number of trials plotted will be this times the bin size used
error_color = 'rgba(169, 169, 169, 0.4)' ## rgba is the only way to get the error band transparent
fig = pf.custom_graph_template(x_title='Trial', y_title='Lick Accuracy (%)', height=500, width=500, titles=[''])
for group in plot_data.columns:
    group_data = plot_data.loc[:, group]
    x_data = np.arange(1, len(group_data[0])+1) * bin_size
    upper = group_data[0] + group_data[1]
    lower = group_data[0] - group_data[1]
    fig.add_trace(go.Scatter(name='Upper Bound', x=x_data[:data_points], y=upper[:data_points], mode='lines',
        marker=dict(color=error_color), line=dict(width=0), showlegend=False, legendgroup=group, opacity=0.7))
    fig.add_trace(go.Scatter(name='Lower Bound', x=x_data[:data_points], y=lower[:data_points], marker=dict(color=error_color),
        line=dict(width=0), mode='lines', fillcolor=error_color, fill='tonexty', showlegend=False, legendgroup=group))
    fig.add_trace(go.Scatter(x=x_data[:data_points], y=group_data[0][:data_points], mode='lines', name=group,
                             line_color=group_colors_dict[group], legendgroup=group))
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(range=[0, 100], dtick=25)
fig.show()
fig.write_image(pjoin(fig_path, f'concatenated_{data_points*bin_size}trials_sham_lession_training.png'))

In [58]:
idx_num = 20 ## mixed anova requires that all subjects have the same number of trials
anova_dict = {'mouse': [], 'genotype': [], 'trial': [], 'accuracy': []}
for mouse in trial_data['mouse']:
    loop_data = trial_data[trial_data['mouse'] == mouse]
    x_data = np.arange(1, len(loop_data['binned_pc'].values[0][:idx_num])+1) * bin_size
    if loop_data['group'].values[0] == 'Sham':
        genotype = 'Sham'
    elif loop_data['group'].values[0] == 'Lesion':
        genotype = 'Lesion'
    for idx, value in enumerate(loop_data['binned_pc'].values[0][:idx_num]):
        anova_dict['mouse'].append(mouse)
        anova_dict['genotype'].append(genotype)
        anova_dict['trial'].append(x_data[idx])
        anova_dict['accuracy'].append(value)
anova_data = pd.DataFrame(anova_dict)
anova_data = anova_data[~pd.isna(anova_data['accuracy'])]
anova_data.mixed_anova(dv='accuracy', within='trial', subject='mouse', between='genotype')

Source            SS  DF1  DF2            MS          F         p-unc  \
0     genotype  10254.502543    1   14  10254.502543  16.094564  1.285945e-03   
1        trial  12422.815866   19  266    653.832414   4.486426  8.209743e-09   
2  Interaction  10463.966094   19  266    550.735058   3.778999  4.984926e-07   

   p-GG-corr       np2       eps sphericity       W-spher   p-spher  
0        NaN  0.534800       NaN        NaN           NaN       NaN  
1   0.004501  0.242688  0.256527      False  4.653156e-16  0.000012  
2        NaN  0.212554       NaN        NaN           NaN       NaN

In [59]:
## Average circle track accuracy up to a minimum number of trials for both groups
bin_size = 4
chance_color = 'darkgrey'
opacity = 0.8
data = {'mouse': [], 'day': [], 'group': [], 'trial_acc': []}
for mouse in os.listdir(circle_path):
    if mouse in bprobe_mice:
        pass
    else:
        mouse_path = pjoin(circle_path, mouse)
        group = 'Sham' if mouse in sham_mice else 'Lesion' 
        for idx, session in enumerate(os.listdir(mouse_path)):
            behav_data = pd.read_feather(pjoin(mouse_path, f'{session}'))
            reward_one, reward_two = np.unique(behav_data['reward_one'])[0], np.unique(behav_data['reward_two'])[0]
            pc = ctb.lick_accuracy(behav_data, reward_one, reward_two, by_trials=True)
            binned_pc = ctb.bin_data(pc, bin_size=bin_size)
            x_data = np.arange(1, len(binned_pc) + 1) * bin_size
            data['mouse'].append(mouse)
            data['day'].append(idx + 1)
            data['group'].append(group)
            data['trial_acc'].append(binned_pc)

trial_acc = pd.DataFrame(data)
group_data = {'Sham': [], 'Lesion': [], 'day': []}
for day in np.unique(trial_acc['day']):
    group_data['Sham'].append(np.nanmean(trial_acc['trial_acc'][(trial_acc['group'] == 'Sham') & (trial_acc['day'] == day)].apply(pd.Series), axis=0))
    group_data['Lesion'].append(np.nanmean(trial_acc['trial_acc'][(trial_acc['group'] == 'Lesion') & (trial_acc['day'] == day)].apply(pd.Series), axis=0))
    group_data['Sham'].append(np.std(trial_acc['trial_acc'][(trial_acc['group'] == 'Sham') & (trial_acc['day'] == day)].apply(pd.Series), axis=0, ddof=1).to_numpy() / np.sqrt(len(trial_acc['trial_acc'][(trial_acc['group'] == 'Sham') & (trial_acc['day'] == day)].apply(pd.Series))))
    group_data['Lesion'].append(np.std(trial_acc['trial_acc'][(trial_acc['group'] == 'Lesion') & (trial_acc['day'] == day)].apply(pd.Series), axis=0, ddof=1).to_numpy() / np.sqrt(len(trial_acc['trial_acc'][(trial_acc['group'] == 'Lesion') & (trial_acc['day'] == day)].apply(pd.Series))))
    group_data['day'].append(day)
    group_data['day'].append(day)
group_df = pd.DataFrame(group_data)

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:983: RuntimeWarning:

Mean of empty slice

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_Behavior/MultiCon_Lesion1/../../circletrack_behavior.py:1061: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/A

In [63]:
only_min_trials = False
error_color = 'rgba(169, 169, 169, 0.4)' ## rgba is the only way to get the error band transparent
fig = pf.custom_graph_template(x_title='', y_title='', height=1000, width=800,
                               rows=4, columns=5, shared_x=True, shared_y=True,
                               titles=[f'Day {x}' for x in np.arange(1, len(np.unique(group_df['day']))+1)])
for idx, day in enumerate(np.unique(group_df['day'])):
    if idx > 19:
        pass
    else:
        plot_data = group_df[group_df['day'] == day]

        if only_min_trials:
            trial_lengths = []
            for group in plot_data.columns[:-1]:
                trial_lengths.append(len(plot_data.loc[:, group].values[0]))
            min_trials = np.min(trial_lengths)
        else:
            min_trials = -1
        
        for group in plot_data.columns[:-1]:
            group_data = plot_data.loc[:, group].values[0][:min_trials]
            upper = plot_data.loc[:, group].values[0][:min_trials] + plot_data.loc[:, group].values[1][:min_trials]
            lower = plot_data.loc[:, group].values[0][:min_trials] - plot_data.loc[:, group].values[1][:min_trials]
            x_data = np.arange(1, len(group_data)+1) * bin_size
            if idx < 5:
                row, col = 1, idx + 1
            elif (idx >= 5) & (idx < 10):
                row, col = 2, idx - 4
            elif (idx >= 10) & (idx < 15):
                row, col = 3, idx - 9
            elif (idx >= 15) & (idx < 20):
                row, col = 4, idx - 14
            
            fig.add_trace(go.Scatter(x=x_data, y=group_data, mode='lines', opacity=opacity,
                                    line_color=group_colors_dict[group], showlegend=False,
                                    legendgroup=group, name=group), row=row, col=col)
            fig.add_trace(go.Scatter(name='Upper Bound', x=x_data, y=upper, mode='lines',
                                    marker=dict(color=error_color), line=dict(width=0), showlegend=False, 
                                    legendgroup=group), row=row, col=col)
            fig.add_trace(go.Scatter(name='Lower Bound', x=x_data, y=lower, marker=dict(color=error_color),
                                    line=dict(width=0), mode='lines', fillcolor=error_color, fill='tonexty', 
                                    showlegend=False, legendgroup=group), row=row, col=col)
fig.add_hline(y=75, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.update_yaxes(title='Lick Accuracy', range=[0, 100], dtick=25, col=1)
fig.update_xaxes(title='Trial', row=5)
fig.show()
if only_min_trials:
    fig.write_image(pjoin(fig_path, 'lick_acc_min_trials_across_groups_shamlesion.png'))
else:
    fig.write_image(pjoin(fig_path, 'lick_acc_across_groups_shamlesion.png'))

### Look at two additional days before sacc'ing for immuno

In [9]:
circletrack_results = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'group_two': [], 'session': [], 
                       'lick_accuracy': [], 'lick_accuracy_thresh3': [], 'rewards': []}
for mouse in os.listdir(circle_path):
    if mouse in bprobe_mice:
        pass
    else:
        mouse_path = pjoin(circle_path, mouse)
        group = 'Sham' if mouse in sham_mice else 'Lesion'
        sex = 'Male' if mouse in male_mice else 'Female'
        grouping = 'Sham Male' if mouse in sham_mice and mouse in male_mice else 'Lesion Male' if mouse not in sham_mice and mouse in male_mice else 'Sham Female' if mouse in sham_mice and mouse not in male_mice else 'Lesion Female'
        for idx, session in enumerate(os.listdir(mouse_path)):
            behav = pd.read_feather(pjoin(mouse_path, f'{session}'))
            behav_data = behav[~behav['probe']]
            reward_one, reward_two = np.unique(behav['reward_one'])[0], np.unique(behav['reward_two'])[0]
            session_pc = ctb.lick_accuracy(behav, port_one=reward_one, port_two=reward_two, lick_threshold=1, by_trials=False)
            session_pc_thresh3 = ctb.lick_accuracy(behav, port_one=reward_one, port_two=reward_two, lick_threshold=3, by_trials=False)
            circletrack_results['mouse'].append(mouse)
            circletrack_results['day'].append(idx+1)
            circletrack_results['group'].append(group)
            circletrack_results['group_two'].append(grouping)
            circletrack_results['sex'].append(sex)
            circletrack_results['session'].append(np.unique(behav['session'])[0])
            circletrack_results['lick_accuracy'].append(session_pc)
            circletrack_results['lick_accuracy_thresh3'].append(session_pc_thresh3)
            circletrack_results['rewards'].append(np.sum(behav_data['water']))
ct_df_all = pd.DataFrame(circletrack_results)

In [12]:
## Plot lick accuracy across days including RM days (thresh1)
fig = pf.plot_behavior_across_days(ct_df_all, x_var='day', y_var='lick_accuracy', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=True, plot_datapoints=False,
                                   x_title='Day', y_title='Lick Accuracy', titles=['Circle Track'], height=500, width=500)
fig.show()
# fig.write_image(pjoin(fig_path, 'lick_accuracy_without_reversal.png'))

In [10]:
## Plot lick accuracy across days including RM days (thresh3)
fig = pf.plot_behavior_across_days(ct_df_all, x_var='day', y_var='lick_accuracy_thresh3', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=True, plot_datapoints=False,
                                   x_title='Day', y_title='Lick Accuracy', titles=['Circle Track'], height=500, width=500)
fig.show()
# fig.write_image(pjoin(fig_path, 'lick_accuracy_without_reversal.png'))

In [26]:
fig = pf.plot_behavior_across_days(ct_df_all, x_var='day', y_var='rewards', groupby_var=['day', 'group'], plot_transitions=None,
                                   marker_color=two_color_plots, avg_color='darkgrey', expert_line=False, chance=False, plot_datapoints=False,
                                   x_title='Day', y_title='Rewards', titles=['Circle Track'], height=500, width=500)
fig.show()

### Look at probe performance for sham vs lesion mice.

In [36]:
probe_results = {'mouse': [], 'day': [], 'group': [], 'sex': [], 'group_two': [], 'session': [], 'lick_accuracy': []}
for mouse in os.listdir(circle_path):
    if mouse in bprobe_mice:
        pass
    else:
        mouse_path = pjoin(circle_path, mouse)
        group = 'Sham' if mouse in sham_mice else 'Lesion'
        sex = 'Male' if mouse in male_mice else 'Female'
        grouping = 'Sham Male' if mouse in sham_mice and mouse in male_mice else 'Lesion Male' if mouse not in sham_mice and mouse in male_mice else 'Sham Female' if mouse in sham_mice and mouse not in male_mice else 'Lesion Female'
        for idx, session in enumerate(os.listdir(mouse_path)):
            behav = pd.read_feather(pjoin(mouse_path, f'{session}'))
            if idx == 0:
                reward_orig_one, reward_orig_two = np.unique(behav['reward_one'])[0], np.unique(behav['reward_two'])[0]
            if any(behav['probe']):
                probe_behav = behav[behav['probe']]
                probe_pc = ctb.lick_accuracy(probe_behav, port_one=reward_orig_one, port_two=reward_orig_two, lick_threshold=1, by_trials=False)
                probe_results['mouse'].append(mouse)
                probe_results['day'].append(idx+1)
                probe_results['group'].append(group)
                probe_results['group_two'].append(grouping)
                probe_results['sex'].append(sex)
                probe_results['session'].append(np.unique(probe_behav['session'])[0])
                probe_results['lick_accuracy'].append(probe_pc)
probe_df = pd.DataFrame(probe_results)

In [42]:
## Plot probe accuracy for sham vs lesion mice
fig = pf.custom_graph_template(x_title='', y_title='Probe Accuracy')
for group in np.unique(probe_df['group']):
    probe_df = probe_df[probe_df['session'] != 'AP']
    group_data = probe_df[probe_df['group'] == group]
    avg_data = group_data.groupby(['session'], as_index=False).agg({'lick_accuracy': ['mean', 'sem']})
    fig.add_trace(go.Scatter(x=avg_data['session'], y=avg_data['lick_accuracy']['mean'], name=group,
                             marker_color=group_colors_dict[group], error_y=dict(type='data', array=avg_data['lick_accuracy']['sem'])))
fig.add_hline(y=25, line_width=1, line_dash='dash', line_color=chance_color, opacity=1)
fig.show()